In [63]:
import pandas as pd

In [64]:
import numpy as np


In [65]:
df = pd.read_csv("hero_selection_final.csv")

In [90]:
#print(df['index_h1'])
matrix1 =np.array(df.loc[:,['match_id', 'Result','index_h1','index_h2','index_h3','index_h4', 'index_h5']])
matrix1

array([[1928898739, 1, '1/28', ..., '3/11', '4/75', '5/94'],
       [1928932285, 1, '1/74', ..., '3/5', '4/70', '5/62'],
       [1928918721, -1, '1/42', ..., '3/32', '4/97', '5/104'],
       ...,
       [1829200497, -1, '1/112', ..., '3/69', '4/39', '5/57'],
       [1829177389, 1, '1/30', ..., '3/6', '4/2', '5/48'],
       [1829220503, -1, '1/29', ..., '3/25', '4/6', '5/72']], dtype=object)

In [91]:
df1 = pd.read_csv("hero_names.csv")

In [92]:
matrix2 =np.array(df1.loc[:,['hero_id', 'Strength','Agility','Intelligence']])

In [93]:
len(matrix2)

113

In [94]:
matrix2[112]

array([113,   0,   1,   0])

In [95]:
import datetime

In [97]:
from itertools import chain

import nltk
import sklearn
import scipy.stats
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import learning_curve, GridSearchCV
#from sklearn.grid_search import RandomizedSearchCV

import sklearn_crfsuite
from sklearn_crfsuite import scorers
from sklearn_crfsuite import metrics

In [109]:
'''This function is written to make the data to get the appropriate data for the features. Data is made using 
3values one is the hero_id, second value that is middle value is for the cummulative values of hero categories,
third one is the index value which stores the hero_category of the next pick.
'''
def tagging(match, hero_matrix):
    final_list=[]
    middle_value=""
    for element in range(2,7):
        middle_tag = ""
        hero_entry = 0
        index_value = 0
        length = len(match[element])
        temp_list = hero_matrix[int(match[element][2:])-1]
        if temp_list[1]==1:
            middle_tag = "St"
        elif temp_list[2]==1:
            middle_tag = "Ag"
        elif temp_list[3]==1:
            middle_tag = "It"
        if element==6:
            index_value = 1000 
        else:
            index_value = int(match[element+1][2:])
            hero_num = hero_matrix[index_value-1]
            if hero_num[1]==1:
                index_value = 1
            elif hero_num[2]==1:
                index_value = 2
            elif hero_num[3]==1:
                index_value = 3
            
        hero_entry = match[element][2:]
        middle_value +=  middle_tag + "/"
        final_list.append((hero_entry, middle_value, index_value))
             
    return final_list
        

dataset = []
for i in range(len(matrix1)):
    dataset.append(tagging(matrix1[i], matrix2))

train_sent = dataset[0:18000]
test_sent = dataset[18000:20000]
test_sent

[[('57', 'It/', 3),
  ('37', 'It/It/', 3),
  ('55', 'It/It/It/', 1),
  ('19', 'It/It/It/St/', 2),
  ('95', 'It/It/It/St/Ag/', 1000)],
 [('36', 'It/', 1),
  ('73', 'It/St/', 3),
  ('37', 'It/St/It/', 1),
  ('29', 'It/St/It/St/', 3),
  ('5', 'It/St/It/St/It/', 1000)],
 [('83', 'St/', 2),
  ('41', 'St/Ag/', 3),
  ('5', 'St/Ag/It/', 3),
  ('74', 'St/Ag/It/It/', 1),
  ('42', 'St/Ag/It/It/St/', 1000)],
 [('85', 'St/', 1),
  ('110', 'St/St/', 3),
  ('84', 'St/St/It/', 2),
  ('67', 'St/St/It/Ag/', 3),
  ('22', 'St/St/It/Ag/It/', 1000)],
 [('44', 'Ag/', 3),
  ('50', 'Ag/It/', 2),
  ('8', 'Ag/It/Ag/', 3),
  ('30', 'Ag/It/Ag/It/', 3),
  ('22', 'Ag/It/Ag/It/It/', 1000)],
 [('5', 'It/', 3),
  ('37', 'It/It/', 1),
  ('18', 'It/It/St/', 2),
  ('70', 'It/It/St/Ag/', 1),
  ('29', 'It/It/St/Ag/St/', 1000)],
 [('68', 'It/', 1),
  ('7', 'It/St/', 2),
  ('72', 'It/St/Ag/', 1),
  ('96', 'It/St/Ag/St/', 2),
  ('106', 'It/St/Ag/St/Ag/', 1000)],
 [('30', 'It/', 2),
  ('44', 'It/Ag/', 2),
  ('70', 'It/Ag/Ag/', 

In [116]:
'''word2features is used to convert the tagged data into feature matrix that will form the input data for 
CRF suite. It returns dictionary values of length 23(total number of features).
'''
def word2features(sent, i):
    word = sent[i][0]
    postag = sent[i][1]
    features = {
        'bias': 1.0,
        'first_2_heros_int': (i==1 and postag[0:2]=='It' and postag[3:5]=='It'),
        'first_hero_It_second_hero_st': (i==1 and postag[0:2]=='It' and postag[3:5]=='St'),
        'first_hero_It_second_hero_Ag': (i==1 and postag[0:2]=='It' and postag[3:5]=='Ag'),
        'alternate_condition_it/st': (i==1 and ((postag[0:2]=='It' and postag[3:5]=='St')or(postag[0:2]=='St' and postag[3:5]=='It'))),
        'alternate_condition_st/ag': (i==1 and ((postag[0:2]=='St' and postag[3:5]=='Ag')or(postag[0:2]=='Ag' and postag[3:5]=='St'))),
        'alternate_condition_it/ag': (i==1 and ((postag[0:2]=='It' and postag[3:5]=='Ag')or(postag[0:2]=='Ag' and postag[3:5]=='It'))),
        'third_hero_st': (i==2 and postag[6:8]=='St'),
        'third_hero_it': (i==2 and postag[6:8]=='It'),
        'third_hero_ag': (i==2 and postag[6:8]=='Ag'),
        'second_hero_int': (i==1 and postag[3:5]=='It'),
        'second_hero_ag': (i==1 and postag[3:5]=='Ag'),
        'second_hero_st': (i==1 and postag[3:5]=='St'),
        'first_hero_int': (i==0 and postag[0:2]=='It'),
        'first_hero_st': (i==0 and postag[0:2]=='St'),
        'first_hero_ag': (i==0 and postag[0:2]=='Ag'),
        'fourth_hero_ag': (i==3 and postag[9:11]=='Ag'),
        'fourth_hero_it': (i==3 and postag[9:11]=='It'),
        'fourth_hero_st': (i==3 and postag[9:11]=='St'),
        'fifth_pick_ag_or_it': (i==4 and ((postag[12:14]=='Ag') or (postag[12:14]=='It'))),  
        'fifth_pick_ag': (i==4 and ((postag[12:14]=='Ag'))), 
        'fifth_pick_it': (i==4 and ((postag[12:14]=='It'))), 
        'fifth_pick_st': (i==4 and ((postag[12:14]=='St'))),   
    }   

   

    return features
   
def sent2features(sent):
    return [word2features(sent, i) for i in range(len(sent))]

def sent2labels(sent):
    return [str(label) for token, postag, label in sent]

<function features at 0x7f9757bcfdd0>


In [117]:
'''Preparation of train and text data'''
sent2features(train_sent[0])
#sent2labels(train_sent[0])
X_train = [sent2features(s) for s in train_sent]
y_train = [sent2labels(s) for s in train_sent]
X_test = [sent2features(s) for s in test_sent]
y_test = [sent2labels(s) for s in test_sent]
len(X_train)
X_train
#y_train

[[{'bias': 1.0,
   'first_2_heros_int': False,
   'first_hero_It_second_hero_st': False,
   'first_hero_It_second_hero_Ag': False,
   'alternate_condition_it/st': False,
   'alternate_condition_st/ag': False,
   'alternate_condition_it/ag': False,
   'third_hero_st': False,
   'third_hero_it': False,
   'third_hero_ag': False,
   'second_hero_int': False,
   'second_hero_ag': False,
   'second_hero_st': False,
   'first_hero_int': False,
   'first_hero_st': True,
   'first_hero_ag': False,
   'fourth_hero_ag': False,
   'fourth_hero_it': False,
   'fourth_hero_st': False,
   'fifth_pick_ag_or_it': False,
   'fifth_pick_ag': False,
   'fifth_pick_it': False,
   'fifth_pick_st': False},
  {'bias': 1.0,
   'first_2_heros_int': False,
   'first_hero_It_second_hero_st': False,
   'first_hero_It_second_hero_Ag': False,
   'alternate_condition_it/st': False,
   'alternate_condition_st/ag': False,
   'alternate_condition_it/ag': False,
   'third_hero_st': False,
   'third_hero_it': False,
   '

In [118]:
'''CRF suite is used to train the model'''
crf = sklearn_crfsuite.CRF(
    algorithm='l2sgd',
    #c1=0.1,
    c2=1,
    max_iterations=1000,
    all_possible_transitions=True
)
crf.fit(X_train, y_train)

CRF(algorithm='l2sgd', all_possible_transitions=True, c2=1, keep_tempfiles=None,
    max_iterations=1000)

In [119]:
'''The total number of labels would be 4. 1 would be for Strength, 2 would be for Agility and 3 would be for 
Intelligence. 1000 is for no category...given to the 5 pick because there is no 6th hero present.
'''
my_labels=['1', '2', '3','1000']

In [120]:
y_pred = crf.predict(X_test)
metrics.flat_f1_score(y_test, y_pred,
                      average='weighted', labels=labels)
sklearn_crfsuite.metrics.flat_accuracy_score(y_test, y_pred)

0.5921

In [122]:
'''Self prediction method is used. Prediction results for 2nd, 3rd, 4th, 5th hero.'''
#y_test
my_ytest = np.array(y_test)
my_ytest_finalhero1 = my_ytest[:,0]
my_ytest_finalhero2 = my_ytest[:,1]
my_ytest_finalhero3 = my_ytest[:,2]
my_ytest_finalhero4 = my_ytest[:,3]
my_ytest_finalhero5 = my_ytest[:,4]
#my_ytest_finalhero
my_ypred = np.array(y_pred)
my_ypred_finalhero1 = my_ypred[:,0]
my_ypred_finalhero2 = my_ypred[:,1]
my_ypred_finalhero3 = my_ypred[:,2]
my_ypred_finalhero4 = my_ypred[:,3]
my_ypred_finalhero5 = my_ypred[:,4]
#my_ypred_finalhero
totals = my_ytest.shape[0]
#totals
num_correct1 = sum(p == t for p, t in zip(my_ypred_finalhero1, my_ytest_finalhero1))
num_correct2 = sum(p == t for p, t in zip(my_ypred_finalhero2, my_ytest_finalhero2))
num_correct3 = sum(p == t for p, t in zip(my_ypred_finalhero3, my_ytest_finalhero3))
num_correct4 = sum(p == t for p, t in zip(my_ypred_finalhero4, my_ytest_finalhero4))
num_correct5 = sum(p == t for p, t in zip(my_ypred_finalhero5, my_ytest_finalhero5))
#num_correct
total1 = (num_correct1/totals)*100
total2 = (num_correct2/totals)*100
total3 = (num_correct3/totals)*100
total4 = (num_correct4/totals)*100
total5 = (num_correct5/totals)*100

print("Prediction accuracy for 2nd hero:", total1)
print("Prediction accuracy for 3rd hero:", total2)
print("Prediction accuracy for 4th hero:", total3)
print("Prediction accuracy for 5th hero:", total4)
#y_pred

Prediction accuracy for 2nd hero: 59.5
Prediction accuracy for 3rd hero: 48.6
Prediction accuracy for 4th hero: 51.349999999999994
Prediction accuracy for 5th hero: 36.6
